In [1]:
# Copyright 2024 Keysight Technologies Inc.

In [2]:
import trueq as tq
import trueq.compilation as tqc

config = tq.Config.from_yaml(
    """
    Mode: ZXZ
    Dimension: 2
    Gates:
    - X(theta):
        Hamiltonian:
          - [X, theta]
    - Z(phi):
        Hamiltonian:
          - [Z, phi]
    - CX:
        Matrix:
          - [1.0, 0.0, 0.0, 0.0]
          - [0.0, 1.0, 0.0, 0.0]
          - [0.0, 0.0, 0.0, 1.0]
          - [0.0, 0.0, 1.0, 0.0]
        Involving:
          (0, 1): 2
          (1, 2): 0
    """
)

In [3]:
custom_passes = [
    tqc.CycleReplacement(
        target=tq.Cycle({(0, 1): tq.Gate.cz}),
        replacement=3 * [tq.Cycle({(0, 1): tq.Gate.cz})],
    ),
    tqc.Merge(max_sys=2),
    tqc.Native2Q(factories=config.factories, mode="ZXZ"),
    tqc.Merge(max_sys=1),
    tqc.Native1Q(factories=config.factories, mode="ZXZ"),
    tqc.RemoveId(),
    tqc.Justify(),
    tqc.InvolvingRestrictions(factories=config.factories),
    tqc.MarkCycles(),
    tqc.Justify(),
    tqc.CycleReplacement(
        target=tq.Cycle({(1, 2): tq.Gate.cx}),
        replacement=tq.Cycle({(1, 2): tq.Gate.cz, 0: tq.Gate.id}, marker=2),
    ),
    tqc.Native2Q(factories=config.factories, mode="ZXZ"),
    tqc.Merge(max_sys=2, marker=2),
    tqc.RemoveId(marker=2),
    tqc.Merge(max_sys=1),
]

# now define a compiler which executes those passes in order
custom_compiler = tqc.Compiler(passes=custom_passes)

In [4]:
circuit = tq.Circuit(
    cycles=[
        tq.Cycle({(0, 1): tq.Gate.cz}),
        tq.Cycle({0: tq.Gate.h, 1: tq.Gate.h}),
        tq.Cycle({(2, 1): tq.Gate.cx}),
        tq.Cycle({(0, 1): tq.Gate.cy, 2: tq.Gate.z}),
    ]
)

circuit.draw(interactive=False)

DisplayWrapper(<svg xmlns="http://w...)

In [5]:
# define a target cycle, CZ on (0, 1), and its replacement, 3 sequential CZs on (0, 1)
target_cycle = tq.Cycle({(0, 1): tq.Gate.cz})
replacement_cycles = 3 * [target_cycle]

# this is the first pass in the custom_compiler
pass1 = tqc.CycleReplacement(target=target_cycle, replacement=replacement_cycles)

# now apply the CycleReplacement pass to the example circuit
compiled_circuit = pass1.apply(circuit)
compiled_circuit.draw(interactive=False)

DisplayWrapper(<svg xmlns="http://w...)

In [6]:
pass2 = tqc.Merge(max_sys=2)
compiled_circuit = pass2.apply(compiled_circuit)
compiled_circuit.draw()

DisplayWrapper(<svg xmlns="http://w...)

In [7]:
pass3 = tqc.Native2Q(factories=config.factories, mode="ZXZ")
compiled_circuit = pass3.apply(compiled_circuit)
compiled_circuit.draw()

DisplayWrapper(<svg xmlns="http://w...)

In [8]:
pass4 = tqc.Merge(max_sys=1)
compiled_circuit = pass4.apply(compiled_circuit)
compiled_circuit.draw()

DisplayWrapper(<svg xmlns="http://w...)

In [9]:
pass5 = tqc.Native1Q(factories=config.factories, mode="ZXZ")
compiled_circuit = pass5.apply(compiled_circuit)
compiled_circuit.draw()

DisplayWrapper(<svg xmlns="http://w...)

In [10]:
pass6 = tqc.RemoveId()
compiled_circuit = pass6.apply(compiled_circuit)
compiled_circuit.draw(interactive=False)

DisplayWrapper(<svg xmlns="http://w...)

In [11]:
# apply a Justify pass to the example circuit
pass7 = tqc.Justify()
compiled_circuit = pass7.apply(compiled_circuit)
compiled_circuit.draw(interactive=False)

DisplayWrapper(<svg xmlns="http://w...)

In [12]:
pass8 = tqc.InvolvingRestrictions(factories=config.factories)
compiled_circuit = pass8.apply(compiled_circuit)
compiled_circuit.draw(interactive=False)

DisplayWrapper(<svg xmlns="http://w...)

In [13]:
pass9 = tqc.MarkCycles()
compiled_circuit = pass9.apply(compiled_circuit)
compiled_circuit.draw(interactive=False)

DisplayWrapper(<svg xmlns="http://w...)

In [14]:
pass10 = tqc.Justify()
compiled_circuit = pass10.apply(compiled_circuit)
compiled_circuit.draw(interactive=False)

DisplayWrapper(<svg xmlns="http://w...)

In [15]:
pass11 = tqc.CycleReplacement(
    target=tq.Cycle({(1, 2): tq.Gate.cx}),
    replacement=tq.Cycle({(1, 2): tq.Gate.cz, 0: tq.Gate.id}, marker=2),
)
compiled_circuit = pass11.apply(compiled_circuit)
compiled_circuit.draw(interactive=False)

DisplayWrapper(<svg xmlns="http://w...)

In [16]:
pass12 = tqc.Native2Q(factories=config.factories, mode="ZXZ")
compiled_circuit = pass12.apply(compiled_circuit)
compiled_circuit.draw(interactive=False)

DisplayWrapper(<svg xmlns="http://w...)

In [17]:
pass13 = tqc.Merge(max_sys=2, marker=2)
compiled_circuit = pass13.apply(compiled_circuit)
compiled_circuit.draw(interactive=False)

DisplayWrapper(<svg xmlns="http://w...)

In [18]:
pass14 = tqc.RemoveId(marker=2)
compiled_circuit = pass14.apply(compiled_circuit)
compiled_circuit.draw(interactive=False)

DisplayWrapper(<svg xmlns="http://w...)

In [19]:
pass15 = tqc.Merge(max_sys=1)
compiled_circuit = pass15.apply(compiled_circuit)
compiled_circuit.draw(interactive=False)

DisplayWrapper(<svg xmlns="http://w...)

In [20]:
compiled_circuit = custom_compiler.compile(circuit)
compiled_circuit.draw(interactive=False)

DisplayWrapper(<svg xmlns="http://w...)